In [1]:
# Import libraries

import pandas as pd
import hvplot.pandas
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt

# machine learning libraries
from pandas.tseries.offsets import DateOffset
from sklearn import svm
from sklearn.metrics import classification_report
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, RobustScaler

In [2]:
# Process Data

# Import data from .csv
btc_metrics_file = 'data/btc_metrics.csv'

btc_df = pd.read_csv(
    btc_metrics_file,
    index_col='date',
    parse_dates=True,
    infer_datetime_format=True
)

display(btc_df.head())
display(btc_df.tail())

price  price_pct_change    a_sopr  puell_multiple  \
date                                                                 
2016-01-01  434.883982               NaN  1.017900        1.430684   
2016-01-02  434.922420          0.000088  1.006339        1.539487   
2016-01-03  430.999798         -0.009019  1.015510        1.525893   
2016-01-04  433.901991          0.006734  1.016040        1.910143   
2016-01-05  433.166599         -0.001695  1.009311        1.654511   

            exchange_netflow  difficulty_compression_band  mvrv_z_score  \
date                                                                      
2016-01-01       3084.261365                     0.149233      0.707518   
2016-01-02      -1595.518899                     0.151165      0.707028   
2016-01-03      12546.093856                     0.153052      0.686532   
2016-01-04       2674.063117                     0.154920      0.699454   
2016-01-05     -17321.634925                     0.156768      0.694940   

            nonzero_balance_addresses  %_utxo_in_profit       nvt      nupl  \
date                                                                          
2016-01-01                  6810666.0          0.829427  7.160297  0.310327   
2016-01-02                  6795517.0          0.825200  7.169680  0.308427   
2016-01-03                  6814427.0          0.814204  7.106625  0.302795   
2016-01-04                  6822805.0          0.821300  7.146942  0.305813   
2016-01-05                  6830653.0          0.812763  7.131518  0.303631   

            stablecoin_supply       rhodl        cvdd       rpv  \
date                                                              
2016-01-01                NaN  336.693607  169.528788  0.000537   
2016-01-02                NaN  322.022994  169.513770  0.000265   
2016-01-03                NaN  328.552037  169.551559  0.000715   
2016-01-04                NaN  313.990154  169.582557  0.000692   
2016-01-05                NaN  324.924804  169.652235  0.000679   

            balanced_price  investor_capitalization  
date                                                 
2016-01-01      232.840772             3.017275e+09  
2016-01-02      232.941445             3.017969e+09  
2016-01-03      233.108481             3.019992e+09  
2016-01-04      233.317436             3.022417e+09  
2016-01-05      233.463981             3.024257e+09

price  price_pct_change    a_sopr  puell_multiple  \
date                                                                   
2021-11-28  57201.708015          0.048763  1.007457        1.165534   
2021-11-29  57816.065292          0.010740  1.023722        1.263554   
2021-11-30  56915.512211         -0.015576  1.007449        1.176360   
2021-12-01  57182.676014          0.004694  1.015373        1.200194   
2021-12-02  56473.963613         -0.012394       NaN             NaN   

            exchange_netflow  difficulty_compression_band  mvrv_z_score  \
date                                                                      
2021-11-28       4600.730240                     0.070742      2.691848   
2021-11-29       6915.509012                     0.069836      2.751011   
2021-11-30         40.726154                     0.068973      2.682099   
2021-12-01      -5845.218444                     0.068153      2.671663   
2021-12-02               NaN                          NaN           NaN   

            nonzero_balance_addresses  %_utxo_in_profit        nvt      nupl  \
date                                                                           
2021-11-28                 39085584.0          0.932517  18.540760  0.571931   
2021-11-29                 39121804.0          0.940265  19.667376  0.575634   
2021-11-30                 39211172.0          0.924972  19.579093  0.568544   
2021-12-01                 39127260.0          0.928958  19.592521  0.569798   
2021-12-02                        NaN               NaN        NaN       NaN   

            stablecoin_supply         rhodl          cvdd       rpv  \
date                                                                  
2021-11-28           0.136625  10635.142280  12120.352583  0.001228   
2021-11-29           0.478233  10245.307366  12136.911568  0.002674   
2021-11-30           0.438603  10413.726880  12153.181435  0.002345   
2021-12-01           0.430659  10447.598656  12176.834671  0.002772   
2021-12-02                NaN           NaN           NaN       NaN   

            balanced_price  investor_capitalization  
date                                                 
2021-11-28    20626.395724             4.282791e+11  
2021-11-29    20670.200219             4.291727e+11  
2021-11-30    20686.550917             4.295484e+11  
2021-12-01    20722.729065             4.303423e+11  
2021-12-02             NaN                      NaN

In [3]:
# Verify datatypes
display(btc_df.dtypes)
display(btc_df.shape)

price                          float64
price_pct_change               float64
a_sopr                         float64
puell_multiple                 float64
exchange_netflow               float64
difficulty_compression_band    float64
mvrv_z_score                   float64
nonzero_balance_addresses      float64
%_utxo_in_profit               float64
nvt                            float64
nupl                           float64
stablecoin_supply              float64
rhodl                          float64
cvdd                           float64
rpv                            float64
balanced_price                 float64
investor_capitalization        float64
dtype: object

(2163, 17)

In [4]:
dataset = btc_df
dataset['nonzero_addy_pct_change'] = btc_df['nonzero_balance_addresses'].pct_change()
dataset['investor_capitalization_pct_change'] = btc_df['investor_capitalization'].pct_change()
dataset['balanced_price_change'] = btc_df['balanced_price'].pct_change()
dataset['cvdd_change'] = btc_df['cvdd'].pct_change()
dataset = btc_df.drop(columns=['cvdd', 'investor_capitalization', 'stablecoin_supply', 'nonzero_balance_addresses', 'balanced_price'])
#dataset.set_index(['date'], inplace=True)
 
dataset.dropna(inplace=True)
dataset

price  price_pct_change    a_sopr  puell_multiple  \
date                                                                   
2016-01-02    434.922420          0.000088  1.006339        1.539487   
2016-01-03    430.999798         -0.009019  1.015510        1.525893   
2016-01-04    433.901991          0.006734  1.016040        1.910143   
2016-01-05    433.166599         -0.001695  1.009311        1.654511   
2016-01-06    429.925349         -0.007483  1.009046        1.478699   
...                  ...               ...       ...             ...   
2021-11-27  54542.063604          0.014515  0.994843        1.204431   
2021-11-28  57201.708015          0.048763  1.007457        1.165534   
2021-11-29  57816.065292          0.010740  1.023722        1.263554   
2021-11-30  56915.512211         -0.015576  1.007449        1.176360   
2021-12-01  57182.676014          0.004694  1.015373        1.200194   

            exchange_netflow  difficulty_compression_band  mvrv_z_score  \
date                                                                      
2016-01-02      -1595.518899                     0.151165      0.707028   
2016-01-03      12546.093856                     0.153052      0.686532   
2016-01-04       2674.063117                     0.154920      0.699454   
2016-01-05     -17321.634925                     0.156768      0.694940   
2016-01-06       2674.220665                     0.158597      0.677147   
...                      ...                          ...           ...   
2021-11-27       2354.575838                     0.071869      2.481278   
2021-11-28       4600.730240                     0.070742      2.691848   
2021-11-29       6915.509012                     0.069836      2.751011   
2021-11-30         40.726154                     0.068973      2.682099   
2021-12-01      -5845.218444                     0.068153      2.671663   

            %_utxo_in_profit        nvt      nupl         rhodl       rpv  \
date                                                                        
2016-01-02          0.825200   7.169680  0.308427    322.022994  0.000265   
2016-01-03          0.814204   7.106625  0.302795    328.552037  0.000715   
2016-01-04          0.821300   7.146942  0.305813    313.990154  0.000692   
2016-01-05          0.812763   7.131518  0.303631    324.924804  0.000679   
2016-01-06          0.805785   7.098181  0.300722    334.869010  0.000581   
...                      ...        ...       ...           ...       ...   
2021-11-27          0.905624  18.295641  0.551288  10562.501897  0.000617   
2021-11-28          0.932517  18.540760  0.571931  10635.142280  0.001228   
2021-11-29          0.940265  19.667376  0.575634  10245.307366  0.002674   
2021-11-30          0.924972  19.579093  0.568544  10413.726880  0.002345   
2021-12-01          0.928958  19.592521  0.569798  10447.598656  0.002772   

            nonzero_addy_pct_change  investor_capitalization_pct_change  \
date                                                                      
2016-01-02                -0.002224                            0.000230   
2016-01-03                 0.002783                            0.000670   
2016-01-04                 0.001229                            0.000803   
2016-01-05                 0.001150                            0.000609   
2016-01-06                 0.001466                            0.000523   
...                             ...                                 ...   
2021-11-27                 0.002525                           -0.000241   
2021-11-28                -0.000093                            0.000494   
2021-11-29                 0.000927                            0.002087   
2021-11-30                 0.002284                            0.000875   
2021-12-01                -0.002140                            0.001848   

            balanced_price_change  cvdd_change  
date                                            
2016-01-02               0.000

In [5]:
dataset.corr()

price  price_pct_change    a_sopr  \
price                               1.000000          0.015233  0.226737   
price_pct_change                    0.015233          1.000000  0.276760   
a_sopr                              0.226737          0.276760  1.000000   
puell_multiple                      0.276152          0.068127  0.585584   
exchange_netflow                   -0.064125         -0.061786  0.022688   
difficulty_compression_band        -0.263964         -0.016819 -0.031340   
mvrv_z_score                        0.457454          0.129785  0.671043   
%_utxo_in_profit                    0.329552          0.143516  0.630609   
nvt                                 0.510658          0.029380  0.230300   
nupl                                0.413139          0.115153  0.637163   
rhodl                               0.152124          0.003910  0.300486   
rpv                                 0.152509          0.166286  0.769128   
nonzero_addy_pct_change            -0.082078          0.063790  0.226223   
investor_capitalization_pct_change  0.114056          0.270292  0.862480   
balanced_price_change               0.138903          0.288096  0.866952   
cvdd_change                         0.074110          0.041639  0.606074   

                                    puell_multiple  exchange_netflow  \
price                                     0.276152         -0.064125   
price_pct_change                          0.068127         -0.061786   
a_sopr                                    0.585584          0.022688   
puell_multiple                            1.000000          0.097275   
exchange_netflow                          0.097275          1.000000   
difficulty_compression_band               0.290740          0.108792   
mvrv_z_score                              0.877820          0.058141   
%_utxo_in_profit                          0.571318         -0.000554   
nvt                                      -0.020045         -0.090413   
nupl                                      0.676496          0.007586   
rhodl                                     0.713785          0.130170   
rpv                                       0.718187          0.169884   
nonzero_addy_pct_change                   0.158148          0.051864   
investor_capitalization_pct_change        0.645303          0.101089   
balanced_price_change                     0.658841          0.072072   
cvdd_change                               0.521533          0.239600   

                                    difficulty_compression_band  mvrv_z_score  \
price                                                 -0.263964      0.457454   
price_pct_change                                      -0.016819      0.129785   
a_sopr                                                -0.031340      0.671043   
puell_multiple                                         0.290740      0.877820   
exchange_netflow                                       0.108792      0.058141   
difficulty_compression_band                            1.000000      0.067330   
mvrv_z_score                                           0.067330      1.000000   
%_utxo_in_profit                                       0.073493      0.738697   
nvt                                                   -0.614609      0.178324   
nupl                                                   0.091013      0.830556   
rhodl                                                  0.393923      0.609466   
rpv                                                    0.097639      0.756492   
nonzero_addy_pct_change                               -0.054657      0.208170   
investor_capitalization_pct_change                     0.046567      0.710770   
balanced_price_change                                  0.028984      0.723019   
cvdd_change                                            0.156812      0.535607   

                                    %_utxo_in_profit       nvt      nupl  \
price                                       0.329552  0.510658  0.4

In [6]:
dataset.hvplot(height=500, width=1200, rot=90)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [7]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2161 entries, 2016-01-02 to 2021-12-01
Data columns (total 16 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   price                               2161 non-null   float64
 1   price_pct_change                    2161 non-null   float64
 2   a_sopr                              2161 non-null   float64
 3   puell_multiple                      2161 non-null   float64
 4   exchange_netflow                    2161 non-null   float64
 5   difficulty_compression_band         2161 non-null   float64
 6   mvrv_z_score                        2161 non-null   float64
 7   %_utxo_in_profit                    2161 non-null   float64
 8   nvt                                 2161 non-null   float64
 9   nupl                                2161 non-null   float64
 10  rhodl                               2161 non-null   float64
 11  rpv                      

In [8]:
# Create the signal
# initialze 'signal' to 0
dataset['signal'] = 0.0

#conditions = [
#    (dataset['price_pct_change'] > 0.01),
#    (dataset['price_pct_change'] <= 0.01) & (dataset['price_pct_change'] >= -0.01),
#    (dataset['price_pct_change'] < -0.01)
#]
    
#values = [1.0, 0.0, -1.0]
    
#dataset['signal'] = np.select(conditions, values)
# When Actual Returns are greater than or equal to 0, generate signal to buy stock long
dataset.loc[(dataset['price_pct_change'] >= 0), 'Signal'] = 1

# When Actual Returns are less than 0, generate signal to sell stock short
dataset.loc[(dataset['price_pct_change'] < 0), 'Signal'] = -1

dataset

price  price_pct_change    a_sopr  puell_multiple  \
date                                                                   
2016-01-02    434.922420          0.000088  1.006339        1.539487   
2016-01-03    430.999798         -0.009019  1.015510        1.525893   
2016-01-04    433.901991          0.006734  1.016040        1.910143   
2016-01-05    433.166599         -0.001695  1.009311        1.654511   
2016-01-06    429.925349         -0.007483  1.009046        1.478699   
...                  ...               ...       ...             ...   
2021-11-27  54542.063604          0.014515  0.994843        1.204431   
2021-11-28  57201.708015          0.048763  1.007457        1.165534   
2021-11-29  57816.065292          0.010740  1.023722        1.263554   
2021-11-30  56915.512211         -0.015576  1.007449        1.176360   
2021-12-01  57182.676014          0.004694  1.015373        1.200194   

            exchange_netflow  difficulty_compression_band  mvrv_z_score  \
date                                                                      
2016-01-02      -1595.518899                     0.151165      0.707028   
2016-01-03      12546.093856                     0.153052      0.686532   
2016-01-04       2674.063117                     0.154920      0.699454   
2016-01-05     -17321.634925                     0.156768      0.694940   
2016-01-06       2674.220665                     0.158597      0.677147   
...                      ...                          ...           ...   
2021-11-27       2354.575838                     0.071869      2.481278   
2021-11-28       4600.730240                     0.070742      2.691848   
2021-11-29       6915.509012                     0.069836      2.751011   
2021-11-30         40.726154                     0.068973      2.682099   
2021-12-01      -5845.218444                     0.068153      2.671663   

            %_utxo_in_profit        nvt      nupl         rhodl       rpv  \
date                                                                        
2016-01-02          0.825200   7.169680  0.308427    322.022994  0.000265   
2016-01-03          0.814204   7.106625  0.302795    328.552037  0.000715   
2016-01-04          0.821300   7.146942  0.305813    313.990154  0.000692   
2016-01-05          0.812763   7.131518  0.303631    324.924804  0.000679   
2016-01-06          0.805785   7.098181  0.300722    334.869010  0.000581   
...                      ...        ...       ...           ...       ...   
2021-11-27          0.905624  18.295641  0.551288  10562.501897  0.000617   
2021-11-28          0.932517  18.540760  0.571931  10635.142280  0.001228   
2021-11-29          0.940265  19.667376  0.575634  10245.307366  0.002674   
2021-11-30          0.924972  19.579093  0.568544  10413.726880  0.002345   
2021-12-01          0.928958  19.592521  0.569798  10447.598656  0.002772   

            nonzero_addy_pct_change  investor_capitalization_pct_change  \
date                                                                      
2016-01-02                -0.002224                            0.000230   
2016-01-03                 0.002783                            0.000670   
2016-01-04                 0.001229                            0.000803   
2016-01-05                 0.001150                            0.000609   
2016-01-06                 0.001466                            0.000523   
...                             ...                                 ...   
2021-11-27                 0.002525                           -0.000241   
2021-11-28                -0.000093                            0.000494   
2021-11-29                 0.000927                            0.002087   
2021-11-30                 0.002284                            0.000875   
2021-12-01                -0.002140                            0.001848   

            balanced_price_change  cvdd_change  signal  Signal  
date                                                           

In [9]:
####### Should probably add in some metrics like rolling averages to smooth the data over a few periods, 
### Perhaps use a short and long window on the price percent changes?

In [10]:
# Create the X & y datasets
y = dataset['signal']
X = dataset.drop(columns=['signal', 'price']).shift().dropna()

X.head()

price_pct_change    a_sopr  puell_multiple  exchange_netflow  \
date                                                                       
2016-01-03          0.000088  1.006339        1.539487      -1595.518899   
2016-01-04         -0.009019  1.015510        1.525893      12546.093856   
2016-01-05          0.006734  1.016040        1.910143       2674.063117   
2016-01-06         -0.001695  1.009311        1.654511     -17321.634925   
2016-01-07         -0.007483  1.009046        1.478699       2674.220665   

            difficulty_compression_band  mvrv_z_score  %_utxo_in_profit  \
date                                                                      
2016-01-03                     0.151165      0.707028          0.825200   
2016-01-04                     0.153052      0.686532          0.814204   
2016-01-05                     0.154920      0.699454          0.821300   
2016-01-06                     0.156768      0.694940          0.812763   
2016-01-07                     0.158597      0.677147          0.805785   

                 nvt      nupl       rhodl       rpv  nonzero_addy_pct_change  \
date                                                                            
2016-01-03  7.169680  0.308427  322.022994  0.000265                -0.002224   
2016-01-04  7.106625  0.302795  328.552037  0.000715                 0.002783   
2016-01-05  7.146942  0.305813  313.990154  0.000692                 0.001229   
2016-01-06  7.131518  0.303631  324.924804  0.000679                 0.001150   
2016-01-07  7.098181  0.300722  334.869010  0.000581                 0.001466   

            investor_capitalization_pct_change  balanced_price_change  \
date                                                                    
2016-01-03                            0.000230               0.000432   
2016-01-04                            0.000670               0.000717   
2016-01-05                            0.000803               0.000896   
2016-01-06                            0.000609               0.000628   
2016-01-07                            0.000523               0.000577   

            cvdd_change  Signal  
date                             
2016-01-03    -0.000089     1.0  
2016-01-04     0.000223    -1.0  
2016-01-05     0.000183     1.0  
2016-01-06     0.000411    -1.0  
2016-01-07     0.000246    -1.0

In [11]:
X.shape

(2160, 16)

In [12]:
y.value_counts()

0.0    2161
Name: signal, dtype: int64

In [13]:
# Select start of training period
training_start = X.index.min()
print(training_start)

# Select the end of the training data with offset
training_end = X.index.min() + DateOffset(months=3)
print(training_end)

# Create training & testing datasets
X_train = X.loc[training_start:training_end]
y_train = y.loc[training_start:training_end]
X_test = X.loc[training_end+DateOffset(days=1):]
y_test = y.loc[training_end+DateOffset(days=1):]
display(X_train.head(2))
display(X_test.head(2))

2016-01-03 00:00:00
2016-04-03 00:00:00


price_pct_change    a_sopr  puell_multiple  exchange_netflow  \
date                                                                       
2016-01-03          0.000088  1.006339        1.539487      -1595.518899   
2016-01-04         -0.009019  1.015510        1.525893      12546.093856   

            difficulty_compression_band  mvrv_z_score  %_utxo_in_profit  \
date                                                                      
2016-01-03                     0.151165      0.707028          0.825200   
2016-01-04                     0.153052      0.686532          0.814204   

                 nvt      nupl       rhodl       rpv  nonzero_addy_pct_change  \
date                                                                            
2016-01-03  7.169680  0.308427  322.022994  0.000265                -0.002224   
2016-01-04  7.106625  0.302795  328.552037  0.000715                 0.002783   

            investor_capitalization_pct_change  balanced_price_change  \
date                                                                    
2016-01-03                             0.00023               0.000432   
2016-01-04                             0.00067               0.000717   

            cvdd_change  Signal  
date                             
2016-01-03    -0.000089     1.0  
2016-01-04     0.000223    -1.0

price_pct_change    a_sopr  puell_multiple  exchange_netflow  \
date                                                                       
2016-04-04          0.000249  1.005139        1.254912      -1281.993959   
2016-04-05         -0.001103  1.004345        1.464511      -3713.297959   

            difficulty_compression_band  mvrv_z_score  %_utxo_in_profit  \
date                                                                      
2016-04-04                     0.146240      0.580823          0.800913   
2016-04-05                     0.144754      0.579057          0.794086   

                 nvt      nupl       rhodl       rpv  nonzero_addy_pct_change  \
date                                                                            
2016-04-04  3.290060  0.261465  759.716033  0.000392                 0.000630   
2016-04-05  3.288296  0.260485  773.519700  0.000369                 0.002167   

            investor_capitalization_pct_change  balanced_price_change  \
date                                                                    
2016-04-04                            0.000307               0.000301   
2016-04-05                            0.000366               0.000455   

            cvdd_change  Signal  
date                             
2016-04-04     0.000453     1.0  
2016-04-05     0.000207    -1.0

In [14]:
# preprocessing
from sklearn.preprocessing import MinMaxScaler, StandardScaler, RobustScaler

# Create the scaler instance
robust_scaler = RobustScaler()
minmax_scaler = MinMaxScaler()
std_scaler = StandardScaler()
                        
# Fit the features for the datasets
X_train_robust = robust_scaler.fit(X_train)
X_test_minmax = minmax_scaler.fit(X_train)
X_train_std = std_scaler.fit(X_train)

# Transform the datasets
X_train_robust = robust_scaler.transform(X_train)
X_test_robust = robust_scaler.transform(X_test)

X_train_minmax = minmax_scaler.transform(X_train)
X_test_minmax = minmax_scaler.transform(X_test)

X_train_std = std_scaler.transform(X_train)
X_test_std = std_scaler.transform(X_test)

In [15]:
# feature extraction

from keras.models import Sequential
from keras.layers import Dense

nn = Sequential()

2021-12-04 15:15:54.264974: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [16]:
X.shape[1]

16

In [42]:
# ML algo 1 - Neural Network

# Define neuron data values
inputs = X.shape[1]
L1_nodes = 20
L2_nodes = 10
L3_nodes = 5

# first layer
nn.add(Dense(units=L1_nodes,input_dim=inputs,activation='selu'))

# second layer
nn.add(Dense(units=L2_nodes,activation='selu'))

# third layer
#nn.add(Dense(units=L3_nodes,activation='softmax'))

# output layer
nn.add(Dense(units=1, activation='elu'))

In [43]:
#nn.summary()

In [45]:
# Compile the model
nn.compile(optimizer='adam', loss='mean_squared_error', metrics=["accuracy"])

# Fit the model
model_robust = nn.fit(X_train_robust, y_train, epochs=200)

Epoch 1/200
3/3 [==============================] - 1s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 2/200
3/3 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 3/200
3/3 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 4/200
3/3 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 5/200
3/3 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 6/200
3/3 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 7/200
3/3 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 8/200
3/3 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 9/200
3/3 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 1.0000
Epoch 10/200
3/3 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accura

In [46]:
# Evaluate the model loss and accuracy metrics using the evaluate method and the test data
model_loss, model_accuracy = nn.evaluate(X_test_robust, y_test, verbose=2)

# Display the evaluation results
print(f"Loss: {model_loss}, Accuracy: {model_accuracy}")

65/65 - 0s - loss: 0.0000e+00 - accuracy: 1.0000 - 361ms/epoch - 6ms/step
Loss: 0.0, Accuracy: 1.0


In [ ]:
# backtest

In [ ]:
# Analyze